Daisy Drive Simulator

n — number of links; can handle up to about 7 before it takes ages
<p>
cost1 — cost of the non-A drives
<p>
cost2 — cost of the A drive
<p>
P — homing efficiency, between 0 and 1
<p>
C — repeated seeding frequency, or 0 if you don’t want repeated seeding
<p>
drive_init — release frequency, between 0 and 1

In [10]:
from IPython.display import display
from IPython.display import HTML
import IPython.core.display as di # Example: di.display_html('<h3>%s:</h3>' % str, raw=True)

# This line will hide code by default when the notebook is exported as HTML
di.display_html('<script>jQuery(function() {if (jQuery("body.notebook_app").length == 0) { jQuery(".input_area").toggle(); jQuery(".prompt").toggle();}});</script>', raw=True)

# This line will add a button to toggle visibility of code blocks, for use with the HTML export version
#di.display_html('''<button onclick="jQuery('.input_area').toggle(); jQuery('.prompt').toggle();">Toggle code</button>''', raw=True)

In [2]:
import percache
cache = percache.Cache("cache.txt")

import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline

In [3]:
@cache
def daisy_drive(n, cost1, cost2, P, C, drive_init, t_max):
    # create file with the input parameters for the matlab function
    s = [n, cost1, cost2, P, C, drive_init, t_max]
    print s
    import csv
    with open('params.txt', 'w') as outfile:
        writer = csv.writer(outfile)
        writer.writerow(s)

    # execute matlab function (bash)
    !rm T.txt
    !rm Y.txt
    !/Applications/MATLAB_R2016a.app/bin/matlab -nodesktop -nosplash -r "cd('/Users/erika/daisy_drive');simulate_applet()"

    # read in matlab output files
    from numpy import genfromtxt
    T = genfromtxt('T.txt', delimiter=',')
    Y = genfromtxt('Y.txt', delimiter=',')
    return(T,Y)

In [4]:
def plot(n, cost1, cost2, C, drive_init):
    fig, ax = plt.subplots(figsize=(4, 3),
                           subplot_kw={'axisbg':'#EEEEEE',
                                       'axisbelow':True})
    ax.grid(color='w', linewidth=2, linestyle='solid')
    
    if C == 1:
        C = drive_init
        
    (T,Y) = daisy_drive(n, cost1, cost2, 1, C, drive_init, 200)

    for i in range(0, n):
        if n > 1:
            Y_i = [b[i] for b in Y]
        else:
            Y_i = Y
        ax.plot(T, Y_i,lw=5, alpha=0.4)
    #ax.set_xlim(0, 10)
    #ax.set_ylim(-1.1, 1.1)
    return fig

In [5]:
# hide silly little matplotlib warning
import warnings
warnings.filterwarnings('ignore')

In [8]:
from ipywidgets import StaticInteract, RangeWidget, RadioWidget

StaticInteract(plot,
               n=RadioWidget([1,2,3,4,5,6]),
               cost1=RadioWidget([0, 0.05, 0.1]),
               cost2=RadioWidget([0.02, 0.1, 0.4]),
               C=RadioWidget([0, 1]),
               drive_init=RadioWidget([0.001, 0.01, 0.1, 1, 0]) )

In [7]:
#plot(3, 0, 0.02, 0, 0.01)

In [9]:
cache.close()